In [1]:
%load_ext autoreload
%autoreload 2
# add . to module name
import sys
sys.path.append('../src/')

In [2]:
from package.logger import Timed, rlog, setup
from package import storage
setup("INFO")

In [3]:
import os
import psutil
import time

import folium
import geopandas as gpd
import pandas as pd
from h3 import h3
from typing import List, Set

from package import strtime
from package.osm import osm
from package.mcr import mcr
from package.mcr.mcr import MCR
from package.mcr.data import MCRGeoData
from package.mcr5.h3 import (
    get_h3_cells_for_nodes,
    get_h3_cells_for_bbox,
    plot_h3_cells_on_folium,
)
from package.mcr5.h3_osm_interaction import get_location_mappings_for_cells
from package.mcr5.mcr5 import MCR5
from package.mcr5.osm import add_nearest_osm_node_id
from package.mcr5.labels import read_labels_for_nodes


In [4]:
city_id = "Koeln"
stops_path = "../data/cleaned/stops.csv"
osm_path = osm.get_osm_path_from_city_id(city_id)

with Timed.info("Reading stops"):
	other_stops_df = storage.read_gdf(stops_path)

if not os.path.exists(osm_path) and city_id:
	rlog.info("Downloading OSM data")
	osm.download_city(city_id, osm_path)
else:
	rlog.info("Using existing OSM data")

osm_reader = osm.new_osm_reader(osm_path)

with Timed.info("Getting OSM graph"):
	nodes, edges = osm.get_graph_for_city_cropped_to_stops(osm_reader, other_stops_df)

[15:34:01] INFO     Reading stops                                                                   ]8;id=264934;file:///tmp/ipykernel_48208/1792129641.py\1792129641.py]8;;\:]8;id=901063;file:///tmp/ipykernel_48208/1792129641.py#5\5]8;;\

           INFO     Reading stops done (0.16 seconds)                                               ]8;id=176441;file:///tmp/ipykernel_48208/1792129641.py\1792129641.py]8;;\:]8;id=250098;file:///tmp/ipykernel_48208/1792129641.py#5\5]8;;\

           INFO     Using existing OSM data                                                        ]8;id=614003;file:///tmp/ipykernel_48208/1792129641.py\1792129641.py]8;;\:]8;id=837841;file:///tmp/ipykernel_48208/1792129641.py#12\12]8;;\

           INFO     Getting OSM graph                                                              ]8;id=257517;file:///tmp/ipykernel_48208/1792129641.py\1792129641.py]8;;\:]8;id=273707;file:///tmp/ipykernel_48208/1792129641.py#16\16]8;;\

           INFO     Loading OSM network from cache                                                 ]8;id=666137;file:///tmp/ipykernel_48208/1792129641.py\1792129641.py]8;;\:]8;id=299748;file:///tmp/ipykernel_48208/1792129641.py#16\16]8;;\

[15:34:02] INFO     Getting OSM graph done (0.91 seconds)                                          ]8;id=251912;file:///tmp/ipykernel_48208/1792129641.py\1792129641.py]8;;\:]8;id=576775;file:///tmp/ipykernel_48208/1792129641.py#16\16]8;;\

In [5]:
h3_cells = get_h3_cells_for_nodes(nodes[["lat", "lon"]].to_dict("records"), 9)
m = folium.Map(location=[50.9333, 6.95], zoom_start=12)
plot_h3_cells_on_folium(h3_cells, m)
m

In [6]:
# Initialize Folium Map centered around Cologne, Germany
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)


# Get unique H3 cells covering the OSM nodes at a given resolution (e.g., 9)
resolution = 9

bbox_cologne_center = [50.92, 6.94, 50.96, 6.98]
h3_cells = get_h3_cells_for_bbox(*bbox_cologne_center, resolution=9)

# Plot H3 cells on the Folium map
plot_h3_cells_on_folium(h3_cells, m)

# draw bbox
folium.Rectangle(
	bounds=[[bbox_cologne_center[0], bbox_cologne_center[1]], [bbox_cologne_center[2], bbox_cologne_center[3]]],
	color='red',
	fill=False,
).add_to(m)

# Show the map
m

In [11]:
h3_cells = get_h3_cells_for_nodes(nodes[["lat", "lon"]].to_dict("records"), 9)
# h3_cells = get_h3_cells_for_bbox(*bbox_cologne_center, resolution=9)

In [12]:
location_mappings, invalid_h3_cells = get_location_mappings_for_cells(list(h3_cells), nodes, 20)

In [13]:
len(location_mappings)

1315

In [14]:
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
plot_h3_cells_on_folium(invalid_h3_cells, m)
m

In [15]:
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
plot_h3_cells_on_folium(map(lambda lm: lm.h3_cell, location_mappings), m)
nodes_by_id = nodes.set_index("id")
for location_mapping in location_mappings:
	node = nodes_by_id.loc[location_mapping.osm_node_id]
	folium.CircleMarker(
		location=(node.lat, node.lon),
		icon=folium.Icon(color="green"),
		radius=1,
		color="red",
	).add_to(m)
m

In [16]:
stops = "../data/cleaned/stops.csv"
city_id = "Koeln"
structs = "../data/structs.pkl"

In [17]:
mcr_geo_data = MCRGeoData(
	stops, structs, city_id
)

[13:38:27] INFO     Reading stops                                                                        ]8;id=555436;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=40727;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#31\31]8;;\

           INFO     Reading stops done (0.04 seconds)                                                    ]8;id=800410;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=526814;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#31\31]8;;\

           INFO     Preparing graphs                                                                     ]8;id=801115;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=456772;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#34\34]8;;\

           INFO     Using existing OSM data                                                              ]8;id=530418;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=695142;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#34\34]8;;\

           INFO     Loading OSM network from cache                                                       ]8;id=319516;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=114083;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#34\34]8;;\

[13:38:49] INFO     Preparing graphs done (22.19 seconds)                                                ]8;id=134220;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=252051;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#34\34]8;;\

           INFO     Creating graph cache                                                                ]8;id=206244;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=421145;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#100\100]8;;\

[13:38:54] INFO     Creating graph cache done (4.25 seconds)                                            ]8;id=210820;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py\data.py]8;;\:]8;id=959814;file:///home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/data.py#100\100]8;;\

In [18]:
mcr5 = MCR5(geo_data=mcr_geo_data, max_processes=12)

In [19]:
mcr5_output_path = "../data/mcr5/Koeln"

In [47]:
errors = mcr5.run(location_mappings, start_time="08:00:00", output_dir=mcr5_output_path)

thread '<unnamed>' panicked at 'called `Result::unwrap()` on an `Err` value: PyErr { type: <class 'TypeError'>, value: TypeError("'str' object cannot be interpreted as an integer"), traceback: None }', src/rs/mlc_adapter.rs:136:18
note: run with `RUST_BACKTRACE=1` environment variable to display a backtrace
Process Process-990:
Traceback (most recent call last):
  File "/home/moritz/miniconda3/envs/mcr-py/lib/python3.10/multiprocessing/process.py", line 314, in _bootstrap
    self.run()
  File "/home/moritz/miniconda3/envs/mcr-py/lib/python3.10/multiprocessing/process.py", line 108, in run
    self._target(*self._args, **self._kwargs)
  File "/home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr5/mcr5.py", line 97, in run_mcr
    mcr_runner.run(
  File "/home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/mcr.py", line 137, in run
    walking_result_bags = mcr_py.run_mlc_with_bags(
pyo3_runtime.PanicException: called `Result::unwrap()` on an `Err` value: PyErr { type: <class 'Ty

Process Process-1344:
Traceback (most recent call last):
  File "/home/moritz/miniconda3/envs/mcr-py/lib/python3.10/multiprocessing/process.py", line 314, in _bootstrap
    self.run()
  File "/home/moritz/miniconda3/envs/mcr-py/lib/python3.10/multiprocessing/process.py", line 108, in run
    self._target(*self._args, **self._kwargs)
  File "/home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr5/mcr5.py", line 97, in run_mcr
    mcr_runner.run(
  File "/home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/mcr.py", line 137, in run
    walking_result_bags = mcr_py.run_mlc_with_bags(
pyo3_runtime.PanicException: called `Result::unwrap()` on an `Err` value: PyErr { type: <class 'TypeError'>, value: TypeError("'str' object cannot be interpreted as an integer"), traceback: None }
thread '<unnamed>' panicked at 'called `Result::unwrap()` on an `Err` value: PyErr { type: <class 'TypeError'>, value: TypeError("'str' object cannot be interpreted as an integer"), traceback: None }', src/rs/

Process Process-1425:
Traceback (most recent call last):
  File "/home/moritz/miniconda3/envs/mcr-py/lib/python3.10/multiprocessing/process.py", line 314, in _bootstrap
    self.run()
  File "/home/moritz/miniconda3/envs/mcr-py/lib/python3.10/multiprocessing/process.py", line 108, in run
    self._target(*self._args, **self._kwargs)
  File "/home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr5/mcr5.py", line 97, in run_mcr
    mcr_runner.run(
  File "/home/moritz/dev/uni/mcr-py/notebooks/../src/package/mcr/mcr.py", line 137, in run
    walking_result_bags = mcr_py.run_mlc_with_bags(
pyo3_runtime.PanicException: called `Result::unwrap()` on an `Err` value: PyErr { type: <class 'TypeError'>, value: TypeError("'str' object cannot be interpreted as an integer"), traceback: None }
thread '<unnamed>' panicked at 'called `Result::unwrap()` on an `Err` value: PyErr { type: <class 'TypeError'>, value: TypeError("'str' object cannot be interpreted as an integer"), traceback: None }', src/rs/

All processes finished.                                  15         


In [50]:
erroneous_osm_node_ids = set(map(lambda e: e[0]["osm_node_id"], errors))
erroneous_osm_node_ids

set()

In [51]:
import overpy

api = overpy.Overpass()

# Define bounding box for Cologne: [south,west,north,east]
bounding_box = "(50.8700,6.8000,51.0500,7.0500)"

# Overpass QL query for supermarkets in the bounding box
overpass_query = f"""
[out:json];
(
    node["shop"="supermarket"]{bounding_box};
    way["shop"="supermarket"]{bounding_box};
    relation["shop"="supermarket"]{bounding_box};
);
out center;
"""

result = api.query(overpass_query)

In [52]:
markets = []
for obj in result.nodes + result.ways + result.relations:
	market = {
		"name": obj.tags.get("name"),
		"id": obj.id,
	}
	if isinstance(obj, overpy.Node):
		market["lat"] = obj.lat
		market["lon"] = obj.lon
	elif isinstance(obj, overpy.Way):
		market["lat"] = obj.center_lat
		market["lon"] = obj.center_lon
	elif isinstance(obj, overpy.Relation):
		market["lat"] = obj.center_lat
		market["lon"] = obj.center_lon
	else:
		raise ValueError(f"Unknown type: {type(obj)}")
	markets.append(market)
		
markets = pd.DataFrame(markets)
markets.head(3)

name         id         lat        lon
0  Netto Marken-Discount   55441040  50.9408725  7.0081399
1               Kaufland  102991868  50.9463208  6.9218135
2  Netto Marken-Discount  232289350  50.9585924  6.9497996

In [53]:
area_of_interest = nodes.geometry.unary_union.convex_hull
markets = gpd.GeoDataFrame(markets, geometry=gpd.points_from_xy(markets.lon, markets.lat))
# only keep markets within area of interest
markets = markets[markets.within(area_of_interest)]
markets

name         id         lat        lon  \
0    Netto Marken-Discount   55441040  50.9408725  7.0081399   
1                 Kaufland  102991868  50.9463208  6.9218135   
2    Netto Marken-Discount  232289350  50.9585924  6.9497996   
3               Netto City  242515981  50.9255261  6.9581475   
4                     REWE  243924635  50.9547763  6.9168738   
..                     ...        ...         ...        ...   
368                   Lidl  798140989  50.9505915  7.0005266   
369            REWE Center  816551392  50.9854625  6.9456900   
370               ALDI Süd  868619074  50.8987225  6.8862791   
371           Edeka Engels  901623455  50.9974473  6.9139239   
373                   Lidl   11026640  50.8934158  6.9033183   

                     geometry  
0    POINT (7.00814 50.94087)  
1    POINT (6.92181 50.94632)  
2    POINT (6.94980 50.95859)  
3    POINT (6.95815 50.92553)  
4    POINT (6.91687 50.95478)  
..                        ...  
368  POINT (7.00053 50.95059)  
369  POINT (6.94569 50.98546)  
370  POINT (6.88628 50.89872)  
371  POINT (6.91392 50.99745)  
373  POINT (6.90332 50.89342)  

[230 rows x 5 columns]

In [54]:
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
for _, market in markets.iterrows():
	folium.CircleMarker(
		location=(market.lat, market.lon),
		popup=market["name"],
		radius=1,
		color="red",
	).add_to(m)
m


In [55]:
markets = add_nearest_osm_node_id(markets, nodes)
markets["count"] = 1
markets

name         id         lat        lon  \
0    Netto Marken-Discount   55441040  50.9408725  7.0081399   
1                 Kaufland  102991868  50.9463208  6.9218135   
2    Netto Marken-Discount  232289350  50.9585924  6.9497996   
3               Netto City  242515981  50.9255261  6.9581475   
4                     REWE  243924635  50.9547763  6.9168738   
..                     ...        ...         ...        ...   
368                   Lidl  798140989  50.9505915  7.0005266   
369            REWE Center  816551392  50.9854625  6.9456900   
370               ALDI Süd  868619074  50.8987225  6.8862791   
371           Edeka Engels  901623455  50.9974473  6.9139239   
373                   Lidl   11026640  50.8934158  6.9033183   

                     geometry  nearest_osm_node_id   distance  count  
0    POINT (7.00814 50.94087)           2725476496   6.737762      1  
1    POINT (6.92181 50.94632)           1246265182   9.802642      1  
2    POINT (6.94980 50.95859)           1680834812  19.672917      1  
3    POINT (6.95815 50.92553)           3890976981  22.818948      1  
4    POINT (6.91687 50.95478)           6908409244  30.201176      1  
..                        ...                  ...        ...    ...  
368  POINT (7.00053 50.95059)           7464862015  27.213849      1  
369  POINT (6.94569 50.98546)          11137319905  26.592059      1  
370  POINT (6.88628 50.89872)           8096600395  41.214910      1  
371  POINT (6.91392 50.99745)           1684392657  69.915888      1  
373  POINT (6.90332 50.89342)           7435945480  35.178416      1  

[230 rows x 8 columns]

In [56]:
labels = read_labels_for_nodes(mcr5_output_path, markets.nearest_osm_node_id.unique())
labels.head(3)

target_id_osm   time  cost  n_transfers human_readable_time  \
302      265913416  34387     0            0            09:33:07   
455     1111698992  31465     0            0            08:44:25   
649       26718385  31443     0            0            08:44:03   

        start_id_hex  
302  891fa1983dbffff  
455  891fa1983dbffff  
649  891fa1983dbffff

In [57]:
labels = labels.merge(
    markets[["count", "nearest_osm_node_id"]],
    left_on="target_id_osm",
    right_on="nearest_osm_node_id",
)
labels.head(3)

target_id_osm   time  cost  n_transfers human_readable_time  \
0      265913416  34387     0            0            09:33:07   
1      265913416  31279     1            1            08:41:19   
2      265913416  31329     0            1            08:42:09   

      start_id_hex  count  nearest_osm_node_id  
0  891fa1983dbffff      1            265913416  
1  891fa1983dbffff      1            265913416  
2  891fa1983dbffff      1            265913416

In [58]:
max_transfers = 1
max_time = strtime.str_time_to_seconds("08:15:00")
max_cost = 0

In [59]:
selected_labels = labels[
	(labels["time"] <= max_time)
	& (labels["n_transfers"] <= max_transfers)
	& (labels["cost"] <= max_cost)
]

In [60]:
reachable = selected_labels.groupby("start_id_hex")["count"].sum()

In [61]:
reachable.max()

141

In [62]:
m = folium.Map(location=[50.9375, 6.9603], zoom_start=12)
plot_h3_cells_on_folium(reachable.to_dict(), m)
# for location_mapping in location_mappings:
# 	node = nodes_by_id.loc[location_mapping.osm_node_id]
# 	folium.CircleMarker(
# 		location=(node.lat, node.lon),
# 		icon=folium.Icon(color="green"),
# 		radius=1,
# 		color="red",
# 	).add_to(m)
m

In [ ]:
from typing import Tuple, TypeVar
import pandas as pd

import networkx as nx
from mcr_py import GraphCache
from package import storage
from package.logger import Timed
from package.osm import osm, graph


ACCURACY = 1
ACCURACY_MULTIPLIER = 10 ** (ACCURACY - 1)

AVG_WALKING_SPEED = 1.4  # m/s
AVG_BIKING_SPEED = 4.0  # m/s

structs_path = "../data/structs.pkl"
stops_path = "../data/cleaned/stops.csv"
city_id = "Koeln"

structs_dict = storage.read_any_dict(structs_path)
with Timed.info("Reading stops"):
    stops_df = storage.read_gdf(stops_path)

with Timed.info("Preparing graphs"):
    osm_reader = osm.get_osm_reader_for_city_id_or_osm_path(city_id, osm_path)
    (
        osm_nodes,
        osm_edges,
    ) = osm.get_graph_for_city_cropped_to_stops(osm_reader, stops_df)

graph: nx.Graph = osm_reader.to_graph(osm_nodes, osm_edges, graph_type="networkx", network_type="walking")  # type: ignore



[17:53:07] INFO     Reading stops                                                                   ]8;id=63286;file:///tmp/ipykernel_64185/665058988.py\665058988.py]8;;\:]8;id=128961;file:///tmp/ipykernel_64185/665058988.py#22\22]8;;\

           INFO     Reading stops done (0.05 seconds)                                               ]8;id=468750;file:///tmp/ipykernel_64185/665058988.py\665058988.py]8;;\:]8;id=886547;file:///tmp/ipykernel_64185/665058988.py#22\22]8;;\

           INFO     Preparing graphs                                                                ]8;id=740397;file:///tmp/ipykernel_64185/665058988.py\665058988.py]8;;\:]8;id=702665;file:///tmp/ipykernel_64185/665058988.py#25\25]8;;\

           INFO     Using existing OSM data                                                         ]8;id=489474;file:///tmp/ipykernel_64185/665058988.py\665058988.py]8;;\:]8;id=297959;file:///tmp/ipykernel_64185/665058988.py#25\25]8;;\

           INFO     Loading OSM network from cache                                                  ]8;id=103310;file:///tmp/ipykernel_64185/665058988.py\665058988.py]8;;\:]8;id=735187;file:///tmp/ipykernel_64185/665058988.py#25\25]8;;\

[17:53:08] INFO     Preparing graphs done (0.98 seconds)                                            ]8;id=423953;file:///tmp/ipykernel_64185/665058988.py\665058988.py]8;;\:]8;id=622947;file:///tmp/ipykernel_64185/665058988.py#25\25]8;;\

In [ ]:
weakly_connected_components = nx.weakly_connected_components(graph)
largest_weakly_connected = max(weakly_connected_components, key=len)

print("Largest weakly connected component:", largest_weakly_connected)

new_graph = graph.subgraph(largest_weakly_connected)
new_graph

Largest weakly connected component: {750518272, 750518274, 1116205896, 750518276, 750518277, 750518281, 1753743374, 4820041744, 4820041745, 4820041746, 4820041747, 4820041748, 4820041749, 1753743384, 4820041753, 4820041754, 4820041755, 1753743386, 1753743392, 4820041764, 4820041765, 4820041766, 4820041767, 4820041768, 4820041769, 260571172, 8629518379, 8629518380, 8629518381, 8629518382, 4820041772, 4820041774, 4820041775, 4820041778, 4820041779, 4820041780, 4820041781, 4820041776, 4820041777, 4820041782, 4820041784, 4820041783, 4820041787, 4820041788, 4820041785, 4820041790, 4820041791, 4820041786, 4820041789, 4820041792, 1139277885, 4820041797, 1546911820, 4820041807, 4778885201, 4820041811, 4778885203, 4820041814, 2419064919, 1546911832, 1546911835, 11060641885, 2419064926, 11060641887, 11060641888, 11060641889, 2419064930, 11060641890, 2419064932, 11060641891, 11060641886, 1546911842, 1546911848, 1546911840, 260571242, 1546911851, 1546911854, 1670381682, 1670381685, 1546911865, 154